Este processo irá realizar a limpeza a agregação dos dados de interação dos Clientes B2B com a plataforma

In [1]:
import pandas as pd
from datetime import datetime
import numpy as np

Limpeza de dados de Clientes do site

In [2]:
df_account = pd.read_csv('Data/Account.csv')

Limpeza de Produtos

In [3]:
df_product = pd.read_csv('Data/Product.csv')

/tmp/ipykernel_31195/4285649015.py:1: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  df_product = pd.read_csv('Data/Product.csv')


Limpeza e Agregação de dados de Pedidos

In [4]:
df_order = pd.read_csv('Data/Order.csv')
df_order['Type'] = 'Order'
df_order['Interaction'] = 2
df_order_item = pd.read_csv('Data/OrderItem.csv')
df_order_interaction = pd.merge(df_order, df_order_item, how='inner', on='OrderId')
df_order_product_interaction = pd.merge(df_order_interaction, df_product, how='inner', on='ProductId')

Limpeza e Agregação de dados de Carrinho de Compras

In [5]:
df_cart = pd.read_csv('Data/WebCart.csv')
df_cart['Type'] = 'Cart'
df_cart['Interaction'] = 1
df_cart_item = pd.read_csv('Data/CartItem.csv')
df_cart_interaction = pd.merge(df_cart, df_cart_item, how='inner', on='WebCartId')
df_cart_product_interaction = pd.merge(df_cart_interaction, df_product, how='inner', on='ProductId')

In [6]:
df_interactions = pd.concat([df_cart_product_interaction, df_order_product_interaction], ignore_index=True)

In [7]:
# Aqui devemos utilizar o inner para remover as contas que não possuem nenhuma interação
df_account_interactions = pd.merge(df_account, df_interactions, how='inner', left_on='Id', right_on='AccountId') 

In [8]:
df_cleaned_interactions = df_account_interactions.drop(['Id', 'CartItemId', 'ProductId', 'Discontinued', 'OrderItemId'], axis=1)

In [9]:
df_cleaned_interactions['OrderDate'] = pd.to_datetime(df_cleaned_interactions['OrderDate'], errors='coerce') 
df_cleaned_interactions['CartDate'] = pd.to_datetime(df_cleaned_interactions['CartDate'].astype(str).str[:10], errors='coerce') 

In [10]:
df_cleaned_interactions['OrderRecency'] = (datetime.now() - df_cleaned_interactions['OrderDate']).dt.days
# Nesta etapa transforma a recência menor que 1 dia em um valor próximo a zero, para que o cálculo de recência não retorne nulo (Divisão por Zero)
df_cleaned_interactions['OrderRecency'] = 1 / df_cleaned_interactions['OrderRecency'].replace(0,0.0000001)

In [11]:
# Cria coluna que indica que interações ocorreram no mês de Setembro (Em produção seria alterado para o mês corrente)
current_month_cart = (
    (df_cleaned_interactions['Type'] == 'Cart') &
    (df_cleaned_interactions['CartDate'].dt.year == 2025) &
    (df_cleaned_interactions['CartDate'].dt.month == 9)
)

current_month_order = (
    (df_cleaned_interactions['Type'] == 'Order') &
    (df_cleaned_interactions['OrderDate'].dt.year == 2025) &
    (df_cleaned_interactions['OrderDate'].dt.month == 9)
)

df_cleaned_interactions['InteractionCurrentMonth'] = np.select(
    [current_month_cart, current_month_order],
    [1, 2],
    default=0
)

In [19]:
current_date = datetime.now()

# Correctly calculate date ranges for 3 and 6 months
three_months_ago = current_date - pd.DateOffset(months=3)
six_months_ago = current_date - pd.DateOffset(months=6)

is_3_month = (df_cleaned_interactions['OrderDate'] >= three_months_ago) &  ~current_month_order
is_6_month = (df_cleaned_interactions['OrderDate'] >= six_months_ago) &  ~current_month_order

# Apply masks to create time-based total columns
df_cleaned_interactions['TotalPrice3Month'] = np.where(is_3_month, df_cleaned_interactions['NetValue'], 0)
df_cleaned_interactions['TotalPrice6Month'] = np.where(is_6_month, df_cleaned_interactions['NetValue'], 0)

df_cleaned_interactions['TotalQuantity3Month'] = np.where(is_3_month, df_cleaned_interactions['Quantity'], 0)
df_cleaned_interactions['TotalQuantity6Month'] = np.where(is_6_month, df_cleaned_interactions['Quantity'], 0)

df_cleaned_interactions['CountOrder3Month'] = np.where(is_3_month, 1, 0)
df_cleaned_interactions['CountOrder6Month'] = np.where(is_6_month, 1, 0)

df_cleaned_interactions['OrderNetValue'] = np.where(df_cleaned_interactions['Type'] == 'Order', df_cleaned_interactions['NetValue'], 0)
df_cleaned_interactions['OrderQuantity'] = np.where(df_cleaned_interactions['Type'] == 'Order', df_cleaned_interactions['Quantity'], 0)

In [20]:
is_3_month = (df_cleaned_interactions['CartDate'] >= three_months_ago) &  ~current_month_cart
is_6_month = (df_cleaned_interactions['CartDate'] >= six_months_ago) &  ~current_month_cart

# Apply masks to create time-based total columns
df_cleaned_interactions['TotalPriceCart3Month'] = np.where(is_3_month, df_cleaned_interactions['NetValue'], 0)
df_cleaned_interactions['TotalPriceCart6Month'] = np.where(is_6_month, df_cleaned_interactions['NetValue'], 0)

df_cleaned_interactions['TotalQuantityCart3Month'] = np.where(is_3_month, df_cleaned_interactions['Quantity'], 0)
df_cleaned_interactions['TotalQuantityCart6Month'] = np.where(is_6_month, df_cleaned_interactions['Quantity'], 0)

df_cleaned_interactions['CountCart3Month'] = np.where(is_3_month, 1, 0)
df_cleaned_interactions['CountCart6Month'] = np.where(is_6_month, 1, 0)

df_cleaned_interactions['CartNetValue'] = np.where(df_cleaned_interactions['Type'] == 'Cart', df_cleaned_interactions['NetValue'], 0)
df_cleaned_interactions['CartQuantity'] = np.where(df_cleaned_interactions['Type'] == 'Cart', df_cleaned_interactions['Quantity'], 0)

In [21]:
df_grouped_interactions = (
    df_cleaned_interactions
        .groupby(['AccountId', 'ProductCode'])
        .agg(
            NetValue=('NetValue', 'sum'),
            Quantity=('Quantity', 'sum'),
            Recency=('OrderRecency', 'min'),
            Weight=('Weight', 'first'),
            ProductLine=('ProductLine', 'first'),
            Size=('Size', 'first'),
            TotalPrice3Month=('TotalPrice3Month', 'sum'),
            TotalPrice6Month=('TotalPrice6Month', 'sum'),
            TotalQuantity3Month=('TotalQuantity3Month', 'sum'),
            TotalQuantity6Month=('TotalQuantity6Month', 'sum'),
            CountOrder3Month=('CountOrder3Month', 'sum'),
            CountOrder6Month=('CountOrder6Month', 'sum'),
            OrderClassification=('InteractionCurrentMonth', 'max'),
            OrderQuantity=('OrderQuantity', 'sum'),
            CartQuantity=('CartQuantity', 'sum'),
            TotalPriceCart3Month=('TotalPriceCart3Month', 'sum'),
            TotalPriceCart6Month=('TotalPriceCart6Month', 'sum'),
            TotalQuantityCart3Month=('TotalQuantityCart3Month', 'sum'),
            TotalQuantityCart6Month=('TotalQuantityCart6Month', 'sum'),
            CountCart3Month=('CountCart3Month', 'sum'),
            CountCart6Month=('CountCart6Month', 'sum'),
            CartNetValue=('CartNetValue', 'sum'),
            OrderNetValue=('OrderNetValue', 'sum'),
            CountOrder=('OrderId', 'nunique'),
            CountCart=('WebCartId', 'nunique'),
        )
).reset_index()

In [23]:
# --- 5. Post-Aggregation Calculations ---
# Calculate Average Tickets, handling potential division by zero
df_grouped_interactions['AverageOrderTicket'] = df_grouped_interactions['OrderNetValue'] / df_grouped_interactions['CountOrder'].replace(0, np.nan)
df_grouped_interactions['AverageOrderTicket3Month'] = df_grouped_interactions['TotalPrice3Month'] / df_grouped_interactions['CountOrder3Month'].replace(0, np.nan)
df_grouped_interactions['AverageOrderTicket6Month'] = df_grouped_interactions['TotalPrice6Month'] / df_grouped_interactions['CountOrder6Month'].replace(0, np.nan)

In [25]:
df_grouped_interactions['AverageCartTicket'] = df_grouped_interactions['CartNetValue'] / df_grouped_interactions['CountCart'].replace(0, np.nan)
df_grouped_interactions['AverageCartTicket3Month'] = df_grouped_interactions['TotalPriceCart3Month'] / df_grouped_interactions['CountCart3Month'].replace(0, np.nan)
df_grouped_interactions['AverageCartTicket6Month'] = df_grouped_interactions['TotalPriceCart6Month'] / df_grouped_interactions['CountCart6Month'].replace(0, np.nan)

In [26]:

# Calculate Product Popularity (Dense Rank by NetValue within each product group)
df_grouped_interactions['ProductPopularity'] = df_grouped_interactions.groupby('ProductCode')['NetValue'].rank(method='dense', ascending=False).astype(int)

In [27]:
# Calculate Total Price and Quantity by Account
df_totals_by_account = df_grouped_interactions.groupby('AccountId').agg(
    TotalPriceByAccount=('OrderNetValue', 'sum'),
    TotalQuantityByAccount=('OrderQuantity', 'sum')
).reset_index()
df_grouped_interactions = pd.merge(df_grouped_interactions, df_totals_by_account, on='AccountId', how='left')

In [28]:
# Calculate Relative Price metrics
total_netvalue_per_product = df_grouped_interactions.groupby('ProductCode')['OrderNetValue'].transform('sum')
df_grouped_interactions['RelativePriceProduct'] = df_grouped_interactions['OrderNetValue'] / total_netvalue_per_product.replace(0, np.nan)

total_netvalue_per_account = df_grouped_interactions.groupby('AccountId')['OrderNetValue'].transform('sum')
df_grouped_interactions['RelativePriceAccount'] = df_grouped_interactions['OrderNetValue'] / total_netvalue_per_account.replace(0, np.nan)

In [29]:
# Round float columns to 2 decimal places
float_cols = df_grouped_interactions.select_dtypes(include=['float64']).columns
df_grouped_interactions[float_cols] = df_grouped_interactions[float_cols].round(2)

In [38]:
df_grouped_interactions.groupby('AccountId').agg(Count=('ProductCode', 'nunique')).sort_values('Count', ascending=False)

Count
AccountId                
0018c00002uQ4MFAA0    468
0018c00002nZUgVAAW    466
001U400000J7k2JIAR    414
001U400000Beo31IAB    392
001U400000TnJwtIAF    390
...                   ...
001U400000LPjltIAD      1
001U4000008SRC0IAO      1
001U4000008Sx2JIAS      1
001U4000008T4zyIAC      1
001U400000LSGU7IAP      1

[12837 rows x 1 columns]

In [39]:
dfs = []

all_products = df_product['ProductCode'].unique()

for acc_id, group in df_grouped_interactions.groupby('AccountId'):
    print(acc_id, group)
    exit
    n_current = len(group)
    n_to_add = max(1, int(n_current * 0.10))  # 10%
    
    random_products = np.random.choice(all_products, size=n_to_add, replace=True)
    
    new_rows = pd.DataFrame({
        'AccountId': [acc_id] * n_to_add,
        'ProductCode': random_products
    })
    
    group = pd.concat([group, new_rows], ignore_index=True)
    dfs.append(group)

df_final = pd.concat(dfs, ignore_index=True)


0018c00002dJJv0AAG             AccountId ProductCode  NetValue  Quantity  Recency  Weight  \
0  0018c00002dJJv0AAG    92015010   4273.80       3.0      0.0    74.8   
1  0018c00002dJJv0AAG    92210010   4540.80       3.0      0.0    76.8   
2  0018c00002dJJv0AAG    92314010   3383.52       2.0      0.0    83.6   

  ProductLine  Size  TotalPrice3Month  TotalPrice6Month  ...  \
0         Lar  None               0.0               0.0  ...   
1         Lar  None               0.0               0.0  ...   
2         Lar  None               0.0               0.0  ...   

   AverageOrderTicket3Month  AverageOrderTicket6Month  AverageCartTicket  \
0                       NaN                       NaN                NaN   
1                       NaN                       NaN                NaN   
2                       NaN                       NaN                NaN   

   AverageCartTicket3Month  AverageCartTicket6Month  ProductPopularity  \
0                      NaN                      

KeyboardInterrupt: 

In [31]:
df_grouped_interactions.to_csv('Data/DataProcessed.csv')